In [1]:
! pip install requests pyarrow datasets duckdb -qU
import os, time, sys, requests, torch, glob
from pathlib import Path
import pandas as pd
import duckdb as ddg
import numpy as np
import pyarrow.parquet as pq
from IPython.display import display, HTML, clear_output
from transformers import GPT2Tokenizer, GPT2LMHeadModel
from datasets import Dataset
from os.path import basename as osb
from huggingface_hub import HfApi, create_repo

from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
email = user_secrets.get_secret("dtdfw_email")
name = user_secrets.get_secret("mysecretname")


import wandb
wandb.init(mode='disabled')

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf 24.8.3 requires cubinlinker, which is not installed.
cudf 24.8.3 requires cupy-cuda11x>=12.0.0, which is not installed.
cudf 24.8.3 requires ptxcompiler, which is not installed.
cuml 24.8.0 requires cupy-cuda11x>=12.0.0, which is not installed.
dask-cudf 24.8.3 requires cupy-cuda11x>=12.0.0, which is not installed.
apache-beam 2.46.0 requires cloudpickle~=2.2.1, but you have cloudpickle 3.0.0 which is incompatible.
apache-beam 2.46.0 requires dill<0.3.2,>=0.3.1.1, but you have dill 0.3.8 which is incompatible.
apache-beam 2.46.0 requires numpy<1.25.0,>=1.14.3, but you have numpy 1.26.4 which is incompatible.
apache-beam 2.46.0 requires pyarrow<10.0.0,>=3.0.0, but you have pyarrow 17.0.0 which is incompatible.
beatrix-jupyterlab 2024.66.154055 requires jupyterlab~=3.6.0, but you have jupyterlab 4.2.5 which is 

In [2]:
work = '/kaggle/working/'

dataset_location = 'https://huggingface.co/datasets/DenyTranDFW/SEC_10K_FSNoNDS_Zip/'

rar_file_download = dataset_location + 'resolve/main/OFFICE_OF_TRADE_AND_SERVICES/RETAIL_EATING_PLACES.rar'
basename = osb(rar_file_download)
rar_file_downloaded = work + basename
rar_file_unrar = work + basename.split('.')[0]

output_csv = work + 'out_csv'
os.makedirs(output_csv, exist_ok=True)

In [3]:
!cd {work}
!sudo apt install libarchive-tools
!wget {rar_file_download} 
clear_output()

In [4]:
!bsdtar -xf {rar_file_downloaded}

In [5]:
duckdb = 'duck.db'
duck = ddg.connect(duckdb)

In [6]:
duck.execute(f'DROP SEQUENCE IF EXISTS question_id_seq;')
duck.execute("CREATE SEQUENCE IF NOT EXISTS id_seq;")

duck.execute(f'''
CREATE TABLE _data (
    id INT DEFAULT nextval('id_seq'),
    tag VARCHAR,
    ddate INT,
    line INT,
    PRIMARY KEY (id)
);''')

In [7]:
parquet_files = [str(x) for x in Path(rar_file_unrar).glob("**/*.parquet")]

In [8]:
for file in parquet_files:
    df = pd.read_parquet(file).sort_values(by=['ddate', 'line'])  
    duck.execute(f"INSERT INTO _data SELECT NEXTVAL('id_seq') AS id, tag, ddate, line FROM df;")

In [9]:
text_data = ' '.join([i[0] for i in list(duck.execute(f"SELECT tag FROM _data ORDER BY id;").df().to_numpy())])

In [10]:
from transformers import Trainer, TrainingArguments

In [11]:
tags = text_data.split()

sequence_length = 50

def create_sequences(tags, seq_length):
    sequences = []
    for i in range(0, len(tags) - seq_length):
        seq = ' '.join(tags[i:i + seq_length])
        sequences.append(seq)
    return sequences

sequences = create_sequences(tags, sequence_length)

In [12]:
import torch
from transformers import GPT2Tokenizer, GPT2LMHeadModel, Trainer, TrainingArguments
from datasets import Dataset
import os

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model_name = 'gpt2'
tokenizer = GPT2Tokenizer.from_pretrained(model_name)
model = GPT2LMHeadModel.from_pretrained(model_name)
model.to(device)

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

/opt/conda/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2SdpaAttention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50257, bias=False)
)

In [13]:
tokenizer.pad_token = tokenizer.eos_token

dataset = Dataset.from_dict({"text": sequences})

def tokenize_function(examples):
    return tokenizer(examples['text'], padding='max_length', truncation=True, max_length=512)

tokenized_datasets = dataset.map(tokenize_function, batched=True, remove_columns=["text"])

Map:   0%|          | 0/122004 [00:00<?, ? examples/s]

In [14]:
def group_texts(examples):
    input_ids = examples['input_ids']
    labels = input_ids.copy()
    return {'input_ids': input_ids, 'labels': labels}

processed_datasets = tokenized_datasets.map(group_texts, batched=True)

Map:   0%|          | 0/122004 [00:00<?, ? examples/s]

In [15]:
training_args = TrainingArguments(
    output_dir="./gpt2-next-tag-prediction",
    overwrite_output_dir=True,
    per_device_train_batch_size=4,
    num_train_epochs=1,
    save_steps=10_000,
    save_total_limit=2,
    prediction_loss_only=True,
    logging_dir="./logs",
    logging_steps=500,
    fp16=torch.cuda.is_available(), 
    learning_rate=5e-5,
    push_to_hub=False,
    report_to=[]
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=processed_datasets,
)

/opt/conda/lib/python3.10/site-packages/accelerate/accelerator.py:494: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


In [16]:
trainer.train()

/opt/conda/lib/python3.10/site-packages/torch/nn/parallel/parallel_apply.py:79: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.device(device), torch.cuda.stream(stream), autocast(enabled=autocast_enabled):
/opt/conda/lib/python3.10/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


/opt/conda/lib/python3.10/site-packages/torch/nn/parallel/parallel_apply.py:79: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.device(device), torch.cuda.stream(stream), autocast(enabled=autocast_enabled):
/opt/conda/lib/python3.10/site-packages/torch/nn/parallel/_functions.py:68: UserWarning: Was asked to gather along dimension 0, but all input tensors were scalars; will instead unsqueeze and return a vector.
  warnings.warn('Was asked to gather along dimension 0, but all '


TrainOutput(global_step=15251, training_loss=0.11975346933497061, metrics={'train_runtime': 12693.6809, 'train_samples_per_second': 9.611, 'train_steps_per_second': 1.201, 'total_flos': 3.1878673072128e+16, 'train_loss': 0.11975346933497061, 'epoch': 1.0})

In [17]:
trainer.save_model("./gpt2-next-tag-prediction")